In [1]:
import tensorflow as tf
import numpy as np

In [2]:
def fc(inputs, num_out, name, activation_fn=None, biased=True):
    w_init = tf.random_normal_initializer(stddev=0.02)
    return tf.layers.dense(inputs=inputs, units=num_out, activation=activation_fn, kernel_initializer=w_init, use_bias=biased, name=name)


def concat(inputs, axis, name):
    return tf.concat(values=inputs, axis=axis, name=name)

def batch_normalization(inputs, is_training, name, activation_fn=None):
    output = tf.layers.batch_normalization(
                    inputs,
                    momentum=0.95,
                    epsilon=1e-5,
                    training=is_training,
                    name=name
                )

    if activation_fn is not None:
        output = activation_fn(output)

    return output

def reshape(inputs, shape, name):
    return tf.reshape(inputs, shape, name)

def Conv2d(input, k_h, k_w, c_o, s_h, s_w, name, activation_fn=None, padding='VALID', biased=False):
    c_i = input.get_shape()[-1]
    w_init = tf.random_normal_initializer(stddev=0.02)

    convolve = lambda i, k: tf.nn.conv2d(i, k, [1, s_h, s_w, 1], padding=padding)
    with tf.variable_scope(name) as scope:
        kernel = tf.get_variable(name='weights', shape=[k_h, k_w, c_i, c_o], initializer=w_init)
        output = convolve(input, kernel)

        if biased:
            biases = tf.get_variable(name='biases', shape=[c_o])
            output = tf.nn.bias_add(output, biases)
        if activation_fn is not None:
            output = activation_fn(output, name=scope.name)

        return output

def add(inputs, name):
    return tf.add_n(inputs, name=name)

def UpSample(inputs, size, method, align_corners, name):
    return tf.image.resize_images(inputs, size, method, align_corners)

def flatten(input, name):
    input_shape = input.get_shape()
    dim = 1
    for d in input_shape[1:].as_list():
        dim *= d
        input = tf.reshape(input, [-1, dim])
    
    return input

class Generator:
    def __init__(self, input_z, input_rnn, is_training, reuse):
        self.input_z = input_z
        self.input_rnn = input_rnn
        self.is_training = is_training
        self.reuse = reuse
        self.t_dim = 128
        self.gf_dim = 128
        self.image_size = 64
        self.c_dim = 3
        self._build_model()

    def _build_model(self):
        s = self.image_size
        s2, s4, s8, s16 = int(s/2), int(s/4), int(s/8), int(s/16)

        gf_dim = self.gf_dim
        t_dim = self.t_dim
        c_dim = self.c_dim

        with tf.variable_scope("generator", reuse=self.reuse):
            net_txt = fc(inputs=self.input_rnn, num_out=t_dim, activation_fn=tf.nn.leaky_relu, name='rnn_fc')
            net_in = concat([self.input_z, net_txt], axis=1, name='concat_z_txt')

            net_h0 = fc(inputs=net_in, num_out=gf_dim*8*s16*s16, name='g_h0/fc', biased=False)
            net_h0 = batch_normalization(net_h0, activation_fn=None, is_training=self.is_training, name='g_h0/batch_norm')
            net_h0 = reshape(net_h0, [-1, s16, s16, gf_dim*8], name='g_h0/reshape')
            
            net = Conv2d(net_h0, 1, 1, gf_dim*2, 1, 1, name='g_h1_res/conv2d')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h1_res/batch_norm')
            net = Conv2d(net, 3, 3, gf_dim*2, 1, 1, name='g_h1_res/conv2d2', padding='SAME')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h1_res/batch_norm2')
            net = Conv2d(net, 3, 3, gf_dim*8, 1, 1, name='g_h1_res/conv2d3', padding='SAME')
            net = batch_normalization(net, activation_fn=None, is_training=self.is_training, name='g_h1_res/batch_norm3')

            net_h1 = add([net_h0, net], name='g_h1_res/add')
            net_h1_output = tf.nn.relu(net_h1)
            
            net_h2 = UpSample(net_h1_output, size=[s8, s8], method=1, align_corners=False, name='g_h2/upsample2d')
            net_h2 = Conv2d(net_h2, 3, 3, gf_dim*4, 1, 1, name='g_h2/conv2d', padding='SAME')
            net_h2 = batch_normalization(net_h2, activation_fn=None, is_training=self.is_training, name='g_h2/batch_norm')

            net = Conv2d(net_h2, 1, 1, gf_dim, 1, 1, name='g_h3_res/conv2d')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h3_res/batch_norm')
            net = Conv2d(net, 3, 3, gf_dim, 1, 1, name='g_h3_res/conv2d2', padding='SAME')
            net = batch_normalization(net, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h3_res/batch_norm2')
            net = Conv2d(net, 3, 3, gf_dim*4, 1, 1, name='g_h3_res/conv2d3', padding='SAME')
            net = batch_normalization(net, activation_fn=None, is_training=self.is_training, name='g_h3_res/batch_norm3')
            
            net_h3 = add([net_h2, net], name='g_h3/add')
            net_h3_outputs = tf.nn.relu(net_h3)

            net_h4 = UpSample(net_h3_outputs, size=[s4, s4], method=1, align_corners=False, name='g_h4/upsample2d')
            net_h4 = Conv2d(net_h4, 3, 3, gf_dim*2, 1, 1, name='g_h4/conv2d', padding='SAME')
            net_h4 = batch_normalization(net_h4, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h4/batch_norm')

            net_h5 = UpSample(net_h4, size=[s2, s2], method=1, align_corners=False, name='g_h5/upsample2d')
            net_h5 = Conv2d(net_h5, 3, 3, gf_dim, 1, 1, name='g_h5/conv2d', padding='SAME')
            net_h5 = batch_normalization(net_h5, activation_fn=tf.nn.relu, is_training=self.is_training, name='g_h5/batch_norm')

            net_ho = UpSample(net_h5, size=[s, s], method=1, align_corners=False, name='g_ho/upsample2d')
            net_ho = Conv2d(net_ho, 3, 3, c_dim, 1, 1, name='g_ho/conv2d', padding='SAME', biased=True) ## biased = True

            self.outputs = tf.nn.tanh(net_ho)
            self.logits = net_ho

class Discriminator:
    def __init__(self, input_image, input_rnn, is_training, reuse):
        self.input_image = input_image
        self.input_rnn = input_rnn
        self.is_training = is_training
        self.reuse = reuse
        self.df_dim = 64
        self.t_dim = 128
        self.image_size = 64
        self._build_model()

    def _build_model(self):
        s = self.image_size
        s2, s4, s8, s16 = int(s/2), int(s/4), int(s/8), int(s/16)

        df_dim = self.df_dim
        t_dim = self.t_dim

        with tf.variable_scope("discriminator", reuse=self.reuse):
            net_h0 = Conv2d(self.input_image, 4, 4, df_dim, 2, 2, name='d_h0/conv2d', activation_fn=tf.nn.leaky_relu, padding='SAME', biased=True)

            net_h1 = Conv2d(net_h0, 4, 4, df_dim*2, 2, 2, name='d_h1/conv2d', padding='SAME')
            net_h1 = batch_normalization(net_h1, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h1/batchnorm')

            net_h2 = Conv2d(net_h1, 4, 4, df_dim*4, 2, 2, name='d_h2/conv2d', padding='SAME')
            net_h2 = batch_normalization(net_h2, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h2/batchnorm')

            net_h3 = Conv2d(net_h2, 4, 4, df_dim*8, 2, 2, name='d_h3/conv2d', padding='SAME')
            net_h3 = batch_normalization(net_h3, activation_fn=None, is_training=self.is_training, name='d_h3/batchnorm')

            net = Conv2d(net_h3, 1, 1, df_dim*2, 1, 1, name='d_h4_res/conv2d')
            net = batch_normalization(net, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h4_res/batchnorm')
            net = Conv2d(net, 3, 3, df_dim*2, 1, 1, name='d_h4_res/conv2d2', padding='SAME')
            net = batch_normalization(net, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h4_res/batchnorm2')
            net = Conv2d(net, 3, 3, df_dim*8, 1, 1, name='d_h4_res/conv2d3', padding='SAME')
            net = batch_normalization(net, activation_fn=None, is_training=self.is_training, name='d_h4_res/batchnorm3')

            net_h4 = add([net_h3, net], name='d_h4/add')
            net_h4_outputs = tf.nn.leaky_relu(net_h4)

            net_txt = fc(self.input_rnn, num_out=t_dim, activation_fn=tf.nn.leaky_relu, name='d_reduce_txt/dense')
            net_txt = tf.expand_dims(net_txt, axis=1, name='d_txt/expanddim1')
            net_txt = tf.expand_dims(net_txt, axis=1, name='d_txt/expanddim2')
            net_txt = tf.tile(net_txt, [1, 4, 4, 1], name='d_txt/tile')
            
            net_h4_concat = concat([net_h4_outputs, net_txt], axis=3, name='d_h3_concat')

            net_h4 = Conv2d(net_h4_concat, 1, 1, df_dim*8, 1, 1, name='d_h3/conv2d_2')
            net_h4 = batch_normalization(net_h4, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='d_h3/batch_norm_2')

            net_ho = Conv2d(net_h4, s16, s16, 1, s16, s16, name='d_ho/conv2d', biased=True) # biased = True

            self.outputs = tf.nn.sigmoid(net_ho)
            self.logits = net_ho

class rnn_encoder:
    def __init__(self, input_seqs, is_training, reuse):
        self.input_seqs = input_seqs
        self.is_training = is_training
        self.reuse = reuse
        self.t_dim = 128  
        self.rnn_hidden_size = 128
        self.vocab_size = 8000
        self.word_embedding_size = 256
        self.keep_prob = 1.0
        self.batch_size = 64
        self._build_model()

    def _build_model(self):
        w_init = tf.random_normal_initializer(stddev=0.02)
        GRUCell = tf.nn.rnn_cell.GRUCell

        with tf.variable_scope("rnnftxt", reuse=self.reuse):
            word_embed_matrix = tf.get_variable('rnn/wordembed', 
                shape=(self.vocab_size, self.word_embedding_size),
                initializer=tf.random_normal_initializer(stddev=0.02),
                dtype=tf.float32)
            embedded_word_ids = tf.nn.embedding_lookup(word_embed_matrix, self.input_seqs)

            # RNN encoder
            GRUCell = tf.nn.rnn_cell.GRUCell(self.t_dim, reuse=self.reuse)
            initial_state = GRUCell.zero_state(self.batch_size, dtype=tf.float32)
            
            rnn_net = tf.nn.dynamic_rnn(cell=GRUCell,
                                    inputs=embedded_word_ids,
                                    initial_state=initial_state,
                                    dtype=np.float32,
                                    time_major=False,
                                    scope='rnn/dynamic')

            self.rnn_net = rnn_net
            self.outputs = rnn_net[0][:, -1, :]

class cnn_encoder:
    def __init__(self, inputs, is_training=True, reuse=False):
        self.inputs = inputs
        self.is_training = is_training
        self.reuse = reuse
        self.df_dim = 64
        self.t_dim = 128
        self._build_model()

    def _build_model(self):
        df_dim = self.df_dim

        with tf.variable_scope('cnnftxt', reuse=self.reuse):
            net_h0 = Conv2d(self.inputs, 4, 4, df_dim, 2, 2, name='cnnf/h0/conv2d', activation_fn=tf.nn.leaky_relu, padding='SAME', biased=True)
            net_h1 = Conv2d(net_h0, 4, 4, df_dim*2, 2, 2, name='cnnf/h1/conv2d', padding='SAME')
            net_h1 = batch_normalization(net_h1, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='cnnf/h1/batch_norm')

            net_h2 = Conv2d(net_h1, 4, 4, df_dim*4, 2, 2, name='cnnf/h2/conv2d', padding='SAME')
            net_h2 = batch_normalization(net_h2, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='cnnf/h2/batch_norm')

            net_h3 = Conv2d(net_h2, 4, 4, df_dim*8, 2, 2, name='cnnf/h3/conv2d', padding='SAME')
            net_h3 = batch_normalization(net_h3, activation_fn=tf.nn.leaky_relu, is_training=self.is_training, name='cnnf/h3/batch_norm')

            net_h4 = flatten(net_h3, name='cnnf/h4/flatten')
            net_h4 = fc(net_h4, num_out=self.t_dim, name='cnnf/h4/embed', biased=False)
        
        self.outputs = net_h4

In [3]:
import pandas as pd
import os
import scipy
from scipy.io import loadmat
import re
import string
import random
import time
import argparse

In [4]:
vocab = np.load(r'C:\Users\Stuti pandey\Documents\text-to-image dictionary\vocab.npy')
print('there are {} vocabularies in total'.format(len(vocab)))

there are 6375 vocabularies in total


In [5]:
word2Id_dict = dict(np.load(r"C:\Users\Stuti pandey\Documents\text-to-image dictionary\word2Id.npy"))
id2word_dict = dict(np.load(r"C:\Users\Stuti pandey\Documents\text-to-image dictionary\id2Word.npy"))

In [6]:
word2Id_dict

{'filamn': '5149',
 'blueish': '3471',
 'werid': '6164',
 'orabg': '5641',
 'rosett': '3957',
 'nuzzl': '58',
 'purpla': '6269',
 'formal': '587',
 'smillar': '5973',
 'int': '4247',
 'alternatimg': '4365',
 'correspond': '5061',
 'watermelon': '4164',
 'backdrop': '3779',
 'wander': '2317',
 'mani': '2474',
 'silli': '1251',
 'pistuil': '5607',
 'steak': '4391',
 'spoke': '4518',
 'attract': '3323',
 'die': '4200',
 'whide': '5152',
 'patern': '4881',
 'lightyellow': '6062',
 'stinryg': '5210',
 'antger': '5877',
 'hipster': '603',
 'subway': '824',
 'woodi': '3360',
 'tent': '281',
 'spike': '2641',
 'fli': '3428',
 'carniv': '1649',
 'eflow': '5630',
 'uneven': '2682',
 'taller': '6202',
 'delegaci': '6156',
 'mechan': '432',
 'mesh': '1559',
 'wave': '3538',
 'chunki': '5489',
 'outlin': '2838',
 'narow': '4746',
 'butteri': '3607',
 'trio': '3195',
 'yllow': '4513',
 'tem': '4511',
 'expos': '2997',
 'coleslaw': '2292',
 'onit': '6270',
 'folag': '5996',
 'holli': '6021',
 'lone':

In [7]:
train_images = np.load(r"C:\Users\Stuti pandey\Documents\text-to-image\train_images.npy", encoding='latin1')
train_captions = np.load(r"C:\Users\Stuti pandey\Documents\text-to-image\train_captions.npy", encoding='latin1')

In [8]:
len(train_images)

7370

In [9]:
len(train_captions)

7370

In [10]:
def IdList2sent(caption):
    sentence = []
    for ID in caption:
        if ID != word2Id_dict['<PAD>']:
            sentence.append(id2word_dict[ID])

    return sentence

print('----example of captions[0]--------')
for caption in train_captions[0]:
    print(IdList2sent(caption))

----example of captions[0]--------
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'brown', 'spot', 'and', 'orang', 'stamen']
['the', 'flower', 'has', 'yellow', 'petal', 'with', 'brown', 'stamen', 'and', 'green', 'pedicel']
['this', 'flower', 'is', 'orang', 'and', 'purpl', 'in', 'color', 'with', 'petal', 'that', 'are', 'spot']
['a', 'curl', 'of', 'yellow', 'petal', 'with', 'purpl', 'leopard', 'spot', 'curl', 'up', 'with', 'stamen', 'hang', 'below']
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'dark', 'spot']
['the', 'petal', 'of', 'the', 'flower', 'are', 'orang', 'in', 'color', 'with', 'brown', 'speckl', 'dot']
['this', 'flower', 'has', 'petal', 'that', 'are', 'tellow', 'and', 'has', 'black', 'spot']
['this', 'flower', 'has', 'long', 'orang', 'petal', 'with', 'dark', 'spot', 'lead', 'to', 'the', 'center']
['this', 'flower', 'has', 'orang', 'petal', 'with', 'dark', 'spot', 'and', 'fold', 'end', 'orient', 'away', 'from', 'a', 'group', 'of', 'long'

In [11]:
captions_list = []
for captions in train_captions:
    assert len(captions) >= 5
    captions_list.append(captions[:5])

In [12]:
train_captions = np.concatenate(captions_list, axis=0) 


In [13]:
n_captions_train = len(train_captions)
n_captions_per_image = 5
n_images_train = len(train_images)

In [14]:
print('Total captions: ', n_captions_train)
print('----example of captions[0] (modified)--------')
for caption in train_captions[:5]:
    print(IdList2sent(caption))

Total captions:  36850
----example of captions[0] (modified)--------
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'brown', 'spot', 'and', 'orang', 'stamen']
['the', 'flower', 'has', 'yellow', 'petal', 'with', 'brown', 'stamen', 'and', 'green', 'pedicel']
['this', 'flower', 'is', 'orang', 'and', 'purpl', 'in', 'color', 'with', 'petal', 'that', 'are', 'spot']
['a', 'curl', 'of', 'yellow', 'petal', 'with', 'purpl', 'leopard', 'spot', 'curl', 'up', 'with', 'stamen', 'hang', 'below']
['this', 'flower', 'has', 'petal', 'that', 'are', 'orang', 'with', 'dark', 'spot']


In [15]:
lr = 0.0002
lr_decay = 0.5      
decay_every = 100  
beta1 = 0.5

In [16]:
z_dim = 512         # Noise dimension
image_size = 64     # 64 x 64
c_dim = 3           # for rgb
batch_size = 64
ni = int(np.ceil(np.sqrt(batch_size)))

In [17]:
### Testing setting
sample_size = batch_size
sample_seed = np.random.normal(loc=0.0, scale=1.0, size=(sample_size, z_dim)).astype(np.float32)

In [18]:
sample_sentence = ["the flower shown has yellow anther red pistil and bright red petals."] * int(sample_size/ni) + \
                  ["this flower has petals that are yellow, white and purple and has dark lines"] * int(sample_size/ni) + \
                  ["the petals on this flower are white with a yellow center"] * int(sample_size/ni) + \
                  ["this flower has a lot of small round pink petals."] * int(sample_size/ni) + \
                  ["this flower is orange in color, and has petals that are ruffled and rounded."] * int(sample_size/ni) + \
                  ["the flower has yellow petals and the center of it is brown."] * int(sample_size/ni) + \
                  ["this flower has petals that are blue and white."] * int(sample_size/ni) +\
                  ["these white flowers have petals that start off white in color and end in a white towards the tips."] * int(sample_size/ni)

In [19]:
def sent2IdList(line, MAX_SEQ_LENGTH=20):
    MAX_SEQ_LIMIT = MAX_SEQ_LENGTH
    padding = 0
    prep_line = re.sub('[%s]' % re.escape(string.punctuation), ' ', line.rstrip())
    prep_line = prep_line.replace('-', ' ')
    prep_line = prep_line.replace('-', ' ')
    prep_line = prep_line.replace('  ', ' ')
    prep_line = prep_line.replace('.', '')
    tokens = prep_line.split(' ')
    tokens = [
        tokens[i] for i in range(len(tokens))
        if tokens[i] != ' ' and tokens[i] != ''
    ]
    l = len(tokens)
    padding = MAX_SEQ_LIMIT - l
    for i in range(padding):
        tokens.append('<PAD>')
    
    line = [
        word2Id_dict[tokens[k]]
        if tokens[k] in word2Id_dict else word2Id_dict['<RARE>']
        for k in range(len(tokens))
    ]

    return line

In [20]:
for i, sent in enumerate(sample_sentence):
    sample_sentence[i] = sent2IdList(sent)

In [21]:
print(sample_sentence[0])


['2435', '2428', '2505', '2431', '2437', '2465', '2446', '2457', '2429', '2455', '2446', '6374', '6372', '6372', '6372', '6372', '6372', '6372', '6372', '6372']


In [22]:
def save(saver, sess, logdir, step):
    model_name = 'model.ckpt'
    checkpoint_path = os.path.join(logdir, model_name)
    
    if not os.path.exists(logdir):
        os.makedirs(logdir)
    saver.save(sess, checkpoint_path, global_step=step)
    print('The checkpoint has been created.')


In [23]:
def load(saver, sess, ckpt_path):
    saver.restore(sess, ckpt_path)
    print("Restored model parameters from {}".format(ckpt_path))

In [24]:
#train
t_real_image = tf.placeholder('float32',[batch_size,image_size,image_size,3],name='real_image')
t_wrong_image = tf.placeholder('float32',[batch_size,image_size,image_size,3],name='wrong_image')
t_real_caption = tf.placeholder(dtype= tf.int64 ,shape=[batch_size,None],name='real_caption_input')
t_wrong_caption = tf.placeholder(dtype=tf.int64,shape=[batch_size,None],name='wrong_caption_input')
t_z = tf.placeholder(tf.float32,[batch_size , z_dim],name='z_noise')

In [25]:
# Training Phase - CNN - RNN mapping
net_cnn = cnn_encoder(t_real_image,is_training=True, reuse=False)
x = net_cnn.outputs
net_rnn = rnn_encoder(t_real_caption,is_training=True, reuse=False)
v= net_rnn.outputs
x_wrong =cnn_encoder(t_wrong_image,is_training=True, reuse=True).outputs
v_wrong = rnn_encoder(t_wrong_caption,is_training=True, reuse=True).outputs


In [26]:
def cosine_similarity(v1, v2):
    cost = tf.reduce_sum(tf.multiply(v1, v2), 1) / (tf.sqrt(tf.reduce_sum(tf.multiply(v1, v1), 1)) * tf.sqrt(tf.reduce_sum(tf.multiply(v2, v2), 1)))
    return cost

In [27]:
alpha =0.2
rnn_loss = tf.reduce_mean(tf.maximum(0.,alpha - cosine_similarity(x,v) + cosine_similarity(x,v_wrong)))+ tf.reduce_mean(tf.maximum(0.,alpha - cosine_similarity(x,v) + cosine_similarity(x_wrong,v)))

In [28]:
# Training Phase - GAN


In [29]:
net_rnn = rnn_encoder(t_real_caption,is_training=False, reuse=True)
net_fake_image = Generator(t_z,net_rnn.outputs,is_training=True, reuse=False)

net_disc_fake = Discriminator(net_fake_image.outputs,net_rnn.outputs,is_training=True, reuse=False)
disc_fake_logits = net_disc_fake.logits

net_disc_real = Discriminator(t_real_image ,net_rnn.outputs,is_training=True, reuse=True)
disc_real_logits = net_disc_real.logits

net_disc_mismatch = Discriminator(t_real_image ,rnn_encoder(t_wrong_caption, is_training=False, reuse=True).outputs,
                                is_training=True, reuse=True)
disc_mismatch_logits = net_disc_mismatch.logits


In [30]:
d_loss1 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_real_logits,     labels=tf.ones_like(disc_real_logits),      name='d1'))
d_loss2 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_mismatch_logits, labels=tf.zeros_like(disc_mismatch_logits), name='d2'))
d_loss3 = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_fake_logits,     labels=tf.zeros_like(disc_fake_logits),     name='d3'))
d_loss = d_loss1 + (d_loss2 + d_loss3) * 0.5

g_loss = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=disc_fake_logits, labels=tf.ones_like(disc_fake_logits), name='g'))


In [31]:
#Testing Phase


In [32]:
net_g = Generator(t_z, rnn_encoder(t_real_caption, is_training=False, reuse=True).outputs,
                    is_training=False, reuse=True)

rnn_vars = [var for var in tf.trainable_variables() if 'rnn' in var.name]
g_vars = [var for var in tf.trainable_variables() if 'generator' in var.name]
d_vars = [var for var in tf.trainable_variables() if 'discrim' in var.name]
cnn_vars = [var for var in tf.trainable_variables() if 'cnn' in var.name]

update_ops_D = [var for var in tf.get_collection(tf.GraphKeys.UPDATE_OPS) if 'discrim' in var.name]
update_ops_G = [var for var in tf.get_collection(tf.GraphKeys.UPDATE_OPS) if 'generator' in var.name]
update_ops_CNN = [var for var in tf.get_collection(tf.GraphKeys.UPDATE_OPS) if 'cnn' in var.name]

print('----------Update_ops_D--------')
for var in update_ops_D:
        print(var.name)
print('----------Update_ops_G--------')
for var in update_ops_G:
        print(var.name)
print('----------Update_ops_CNN--------')
for var in update_ops_CNN:
        print(var.name)


----------Update_ops_D--------
discriminator/d_h1/batchnorm/AssignMovingAvg
discriminator/d_h1/batchnorm/AssignMovingAvg_1
discriminator/d_h2/batchnorm/AssignMovingAvg
discriminator/d_h2/batchnorm/AssignMovingAvg_1
discriminator/d_h3/batchnorm/AssignMovingAvg
discriminator/d_h3/batchnorm/AssignMovingAvg_1
discriminator/d_h4_res/batchnorm/AssignMovingAvg
discriminator/d_h4_res/batchnorm/AssignMovingAvg_1
discriminator/d_h4_res/batchnorm2/AssignMovingAvg
discriminator/d_h4_res/batchnorm2/AssignMovingAvg_1
discriminator/d_h4_res/batchnorm3/AssignMovingAvg
discriminator/d_h4_res/batchnorm3/AssignMovingAvg_1
discriminator/d_h3/batch_norm_2/AssignMovingAvg
discriminator/d_h3/batch_norm_2/AssignMovingAvg_1
discriminator_1/d_h1/batchnorm/AssignMovingAvg
discriminator_1/d_h1/batchnorm/AssignMovingAvg_1
discriminator_1/d_h2/batchnorm/AssignMovingAvg
discriminator_1/d_h2/batchnorm/AssignMovingAvg_1
discriminator_1/d_h3/batchnorm/AssignMovingAvg
discriminator_1/d_h3/batchnorm/AssignMovingAvg_1
dis

In [33]:
checkpoint_dir = './checkpoint'


In [34]:
with tf.variable_scope('learning_rate'):
        lr_v = tf.Variable(lr, trainable=False)

with tf.control_dependencies(update_ops_D):
        d_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(d_loss, var_list=d_vars)

with tf.control_dependencies(update_ops_G):
    g_optim = tf.train.AdamOptimizer(lr_v, beta1=beta1).minimize(g_loss, var_list=g_vars)

with tf.control_dependencies(update_ops_CNN):
        grads, _ = tf.clip_by_global_norm(tf.gradients(rnn_loss, rnn_vars + cnn_vars), 10)
        optimizer = tf.train.AdamOptimizer(lr_v, beta1=beta1)
        rnn_optim = optimizer.apply_gradients(zip(grads, rnn_vars + cnn_vars))

sess = tf.Session(config=tf.ConfigProto(allow_soft_placement=True))
init = tf.global_variables_initializer()
sess.run(init)

saver = tf.train.Saver(var_list=tf.global_variables(), max_to_keep=5)

ckpt = tf.train.get_checkpoint_state(checkpoint_dir)
if ckpt and ckpt.model_checkpoint_path:
    loader = tf.train.Saver(var_list=tf.global_variables())
    load_step = int(os.path.basename(ckpt.model_checkpoint_path).split('-')[1])
    load(loader, sess, ckpt.model_checkpoint_path)
else:
    print('no checkpoints find.')



INFO:tensorflow:Restoring parameters from ./checkpoint\model.ckpt-110
Restored model parameters from ./checkpoint\model.ckpt-110


In [35]:
import threading
import scipy.ndimage as ndi
from skimage import transform
from skimage import exposure
import skimage

In [36]:
def apply_transform(x, transform_matrix, channel_index=2, fill_mode='nearest', cval=0., order=1):
    x = np.rollaxis(x, channel_index, 0)
    final_affine_matrix = transform_matrix[:2, :2]
    final_offset = transform_matrix[:2, 2]
    channel_images = [ndi.interpolation.affine_transform(x_channel, final_affine_matrix,
                      final_offset, order=order, mode=fill_mode, cval=cval) for x_channel in x]
    x = np.stack(channel_images, axis=0)
    x = np.rollaxis(x, 0, channel_index+1)
    return x

def transform_matrix_offset_center(matrix, x, y):
    o_x = float(x) / 2 + 0.5
    o_y = float(y) / 2 + 0.5
    offset_matrix = np.array([[1, 0, o_x], [0, 1, o_y], [0, 0, 1]])
    reset_matrix = np.array([[1, 0, -o_x], [0, 1, -o_y], [0, 0, 1]])
    transform_matrix = np.dot(np.dot(offset_matrix, matrix), reset_matrix)
    return transform_matrix

def get_random_int(min=0, max=10, number=5):
    """Return a list of random integer by the given range and quantity.
    Examples
    ---------
    >>> r = get_random_int(min=0, max=10, number=5)
    ... [10, 2, 3, 3, 7]
    """
    return [random.randint(min,max) for p in range(0,number)]

def threading_data(data=None, fn=None, **kwargs):
    def apply_fn(results, i, data, kwargs):
        results[i] = fn(data, **kwargs)

    ## start multi-threaded reading.
    results = [None] * len(data) ## preallocate result list
    threads = []
    for i in range(len(data)):
        t = threading.Thread(
                        name='threading_and_return',
                        target=apply_fn,
                        args=(results, i, data[i], kwargs)
                        )
        t.start()
        threads.append(t)

    for t in threads:
        t.join()

    return np.asarray(results)

def flip_axis(x, axis, is_random=False):
    if is_random:
        factor = np.random.uniform(-1, 1)
        if factor > 0:
            x = np.asarray(x).swapaxes(axis, 0)
            x = x[::-1, ...]
            x = x.swapaxes(0, axis)
            return x
        else:
            return x
    else:
        x = np.asarray(x).swapaxes(axis, 0)
        x = x[::-1, ...]
        x = x.swapaxes(0, axis)
        return x
    
def imresize(x, size=[100, 100], interp='bilinear', mode=None):
    if x.shape[-1] == 1:
        # greyscale
        x = scipy.misc.imresize(x[:,:,0], size, interp=interp, mode=mode)
        return x[:, :, np.newaxis]
    elif x.shape[-1] == 3:
        # rgb, bgr ..
        return scipy.misc.imresize(x, size, interp=interp, mode=mode)
    else:
        raise Exception("Unsupported channel %d" % x.shape[-1])

def rotation(x, rg=20, is_random=False, row_index=0, col_index=1, channel_index=2,
                    fill_mode='nearest', cval=0.):
    if is_random:
        theta = np.pi / 180 * np.random.uniform(-rg, rg)
    else:
        theta = np.pi /180 * rg
    rotation_matrix = np.array([[np.cos(theta), -np.sin(theta), 0],
                                [np.sin(theta), np.cos(theta), 0],
                                [0, 0, 1]])

    h, w = x.shape[row_index], x.shape[col_index]
    transform_matrix = transform_matrix_offset_center(rotation_matrix, h, w)
    x = apply_transform(x, transform_matrix, channel_index, fill_mode, cval)
    return x

def crop(x, wrg, hrg, is_random=False, row_index=0, col_index=1, channel_index=2):
    h, w = x.shape[row_index], x.shape[col_index]
    assert (h > hrg) and (w > wrg), "The size of cropping should smaller than the original image"
    if is_random:
        h_offset = int(np.random.uniform(0, h-hrg) -1)
        w_offset = int(np.random.uniform(0, w-wrg) -1)
        return x[h_offset: hrg+h_offset ,w_offset: wrg+w_offset]
    else:   # central crop
        h_offset = int(np.floor((h - hrg)/2.))
        w_offset = int(np.floor((w - wrg)/2.))
        h_end = h_offset + hrg
        w_end = w_offset + wrg
        return x[h_offset: h_end, w_offset: w_end]        
        

def prepro_img(x, mode=None):
    # rescale [0, 255] --> (-1, 1), random flip, crop, rotate

    if mode=='train':
        x = flip_axis(x, axis=1, is_random=True)
        x = rotation(x, rg=16, is_random=True, fill_mode='nearest')
        x = imresize(x, size=[64+15, 64+15], interp='bilinear', mode=None)
        x = crop(x, wrg=64, hrg=64, is_random=True)
        x = x / (255. / 2.)
        x = x - 1.
        # x = x * 0.9999

    return x

In [37]:
## Save images
def merge(images, size):
    h, w = images.shape[1], images.shape[2]
    img = np.zeros((h * size[0], w * size[1], 3))
    for idx, image in enumerate(images):
        i = idx % size[1]
        j = idx // size[1]
        img[j*h:j*h+h, i*w:i*w+w, :] = image
    return img

def imsave(images, size, path):
    return scipy.misc.imsave(path, merge(images, size))

def save_images(images, size, image_path):
    return imsave(images, size, image_path)

In [38]:
n_epoch = 300
n_batch_epoch = int(n_images_train / batch_size)
for epoch in range(n_epoch):
    start_time = time.time()

    if epoch !=0 and (epoch % decay_every == 0):
            new_lr_decay = lr_decay ** (epoch // decay_every)
            sess.run(tf.assign(lr_v, lr * new_lr_decay))
            log = " ** new learning rate: %f" % (lr * new_lr_decay)
            print(log)
            
    elif epoch == 0:
            log = " ** init lr: %f  decay_every_epoch: %d, lr_decay: %f" % (lr, decay_every, lr_decay)
            print(log)

    for step in range(n_batch_epoch):
        step_time = time.time()

        ## get matched text & image
        idexs = get_random_int(min=0, max=n_captions_train-1, number=batch_size)
        b_real_caption = train_captions[idexs]
        b_real_images = train_images[np.floor(np.asarray(idexs).astype('float')/n_captions_per_image).astype('int')]

        """ check for loading right images
        save_images(b_real_images, [ni, ni], 'train_samples/train_00.png')
        for caption in b_real_caption[:8]:
        print(IdList2sent(caption))
        exit()
        """

        ## get wrong caption & wrong image
        idexs = get_random_int(min=0, max=n_captions_train-1, number=batch_size)
        b_wrong_caption = train_captions[idexs]
        idexs2 = get_random_int(min=0, max=n_images_train-1, number=batch_size)
        b_wrong_images = train_images[idexs2]

        ## get noise
        b_z = np.random.normal(loc=0.0, scale=1.0, size=(batch_size, z_dim)).astype(np.float32)

        b_real_images = threading_data(b_real_images, prepro_img, mode='train')   # [0, 255] --> [-1, 1] + augmentation
        b_wrong_images = threading_data(b_wrong_images, prepro_img, mode='train')

        ## update RNN
        if epoch < 80:
            errRNN, _ = sess.run([rnn_loss, rnn_optim], feed_dict={
                                                t_real_image : b_real_images,
                                                t_wrong_image : b_wrong_images,
                                                t_real_caption : b_real_caption,
                                                t_wrong_caption : b_wrong_caption})
        else:
            errRNN = 0

        ## updates D
        errD, _ = sess.run([d_loss, d_optim], feed_dict={
                            t_real_image : b_real_images,
                            t_wrong_caption : b_wrong_caption,
                            t_real_caption : b_real_caption,
                            t_z : b_z})
        ## updates G
        errG, _ = sess.run([g_loss, g_optim], feed_dict={
                            t_real_caption : b_real_caption,
                            t_z : b_z})

        print("Epoch: [%2d/%2d] [%4d/%4d] time: %4.4fs, d_loss: %.8f, g_loss: %.8f, rnn_loss: %.8f" \
                        % (epoch, n_epoch, step, n_batch_epoch, time.time() - step_time, errD, errG, errRNN))
        
        if (epoch + 1) % 1 == 0:
            print(" ** Epoch %d took %fs" % (epoch, time.time()-start_time))
            img_gen, rnn_out = sess.run([net_g.outputs, net_rnn.outputs], feed_dict={
                                        t_real_caption : sample_sentence,
                                        t_z : sample_seed})

            save_images(img_gen, [ni, ni],r"C:\Users\Stuti pandey\Documents\train_samples\train_{:02d}.png".format(epoch))

        if (epoch != 0) and (epoch % 10) == 0:
            save(saver, sess, checkpoint_dir, epoch)
            print("[*] Save checkpoints SUCCESS!")

testData = os.path.join('dataset', 'testData.pkl')

 ** init lr: 0.000200  decay_every_epoch: 100, lr_decay: 0.500000
Epoch: [ 0/300] [   0/ 115] time: 18.2961s, d_loss: 0.57489455, g_loss: 1.45441294, rnn_loss: 0.09782819
 ** Epoch 0 took 18.296147s
Epoch: [ 0/300] [   1/ 115] time: 0.7530s, d_loss: 0.39089203, g_loss: 1.39505672, rnn_loss: 0.06653035
 ** Epoch 0 took 19.472326s
Epoch: [ 0/300] [   2/ 115] time: 0.7492s, d_loss: 0.53552413, g_loss: 1.57248664, rnn_loss: 0.09114759
 ** Epoch 0 took 20.427936s
Epoch: [ 0/300] [   3/ 115] time: 0.7810s, d_loss: 0.42855114, g_loss: 2.27682161, rnn_loss: 0.08244123
 ** Epoch 0 took 21.419360s
Epoch: [ 0/300] [   4/ 115] time: 0.7839s, d_loss: 0.56539333, g_loss: 2.36425972, rnn_loss: 0.09971081
 ** Epoch 0 took 22.470567s
Epoch: [ 0/300] [   5/ 115] time: 0.7790s, d_loss: 0.19272706, g_loss: 2.77141714, rnn_loss: 0.09440177
 ** Epoch 0 took 23.455047s
Epoch: [ 0/300] [   6/ 115] time: 0.7790s, d_loss: 0.33873001, g_loss: 1.89321911, rnn_loss: 0.07889076
 ** Epoch 0 took 24.484298s
Epoch: [ 

Epoch: [ 0/300] [  62/ 115] time: 0.7869s, d_loss: 0.35483506, g_loss: 2.08899975, rnn_loss: 0.05872162
 ** Epoch 0 took 79.319683s
Epoch: [ 0/300] [  63/ 115] time: 0.7570s, d_loss: 0.56320125, g_loss: 1.88962483, rnn_loss: 0.05327441
 ** Epoch 0 took 80.268186s
Epoch: [ 0/300] [  64/ 115] time: 0.7710s, d_loss: 0.28918988, g_loss: 2.19664955, rnn_loss: 0.05804366
 ** Epoch 0 took 81.242564s
Epoch: [ 0/300] [  65/ 115] time: 0.7679s, d_loss: 0.35677391, g_loss: 1.85649037, rnn_loss: 0.04920596
 ** Epoch 0 took 82.207018s
Epoch: [ 0/300] [  66/ 115] time: 0.7563s, d_loss: 0.26245087, g_loss: 2.08902407, rnn_loss: 0.07235255
 ** Epoch 0 took 83.160732s
Epoch: [ 0/300] [  67/ 115] time: 0.8372s, d_loss: 0.59702700, g_loss: 2.15964317, rnn_loss: 0.02801206
 ** Epoch 0 took 84.194934s
Epoch: [ 0/300] [  68/ 115] time: 0.7470s, d_loss: 0.40496224, g_loss: 1.86222720, rnn_loss: 0.08181980
 ** Epoch 0 took 85.142407s
Epoch: [ 0/300] [  69/ 115] time: 0.7600s, d_loss: 0.39310902, g_loss: 1.933

Epoch: [ 1/300] [   9/ 115] time: 0.7543s, d_loss: 0.60690749, g_loss: 2.73541737, rnn_loss: 0.07620625
 ** Epoch 1 took 9.613708s
Epoch: [ 1/300] [  10/ 115] time: 0.7571s, d_loss: 0.33102512, g_loss: 2.79495096, rnn_loss: 0.10928931
 ** Epoch 1 took 10.571192s
Epoch: [ 1/300] [  11/ 115] time: 0.7600s, d_loss: 0.71316457, g_loss: 1.02395082, rnn_loss: 0.06901388
 ** Epoch 1 took 11.530642s
Epoch: [ 1/300] [  12/ 115] time: 0.7599s, d_loss: 0.44451079, g_loss: 1.55551887, rnn_loss: 0.07097144
 ** Epoch 1 took 12.490062s
Epoch: [ 1/300] [  13/ 115] time: 0.7630s, d_loss: 0.66558027, g_loss: 2.15361261, rnn_loss: 0.06010817
 ** Epoch 1 took 13.453512s
Epoch: [ 1/300] [  14/ 115] time: 0.7421s, d_loss: 0.19579887, g_loss: 3.04693365, rnn_loss: 0.10382054
 ** Epoch 1 took 14.409045s
Epoch: [ 1/300] [  15/ 115] time: 0.7510s, d_loss: 0.43893206, g_loss: 1.62473249, rnn_loss: 0.13859233
 ** Epoch 1 took 15.360519s
Epoch: [ 1/300] [  16/ 115] time: 0.7680s, d_loss: 0.30378830, g_loss: 1.9268

Epoch: [ 1/300] [  72/ 115] time: 0.7400s, d_loss: 0.44898853, g_loss: 1.36850297, rnn_loss: 0.08671016
 ** Epoch 1 took 70.558104s
Epoch: [ 1/300] [  73/ 115] time: 0.7447s, d_loss: 0.49563384, g_loss: 1.56871319, rnn_loss: 0.09774218
 ** Epoch 1 took 71.506279s
Epoch: [ 1/300] [  74/ 115] time: 0.7681s, d_loss: 0.52507746, g_loss: 1.90740860, rnn_loss: 0.10426842
 ** Epoch 1 took 72.476796s
Epoch: [ 1/300] [  75/ 115] time: 0.7461s, d_loss: 0.52073550, g_loss: 2.50127840, rnn_loss: 0.05947842
 ** Epoch 1 took 73.420384s
Epoch: [ 1/300] [  76/ 115] time: 0.7670s, d_loss: 0.63373715, g_loss: 1.40538311, rnn_loss: 0.08451454
 ** Epoch 1 took 74.380784s
Epoch: [ 1/300] [  77/ 115] time: 0.7540s, d_loss: 0.42112923, g_loss: 1.24338686, rnn_loss: 0.08991948
 ** Epoch 1 took 75.325306s
Epoch: [ 1/300] [  78/ 115] time: 0.7590s, d_loss: 0.41562480, g_loss: 1.81138361, rnn_loss: 0.06460770
 ** Epoch 1 took 76.277744s
Epoch: [ 1/300] [  79/ 115] time: 0.7480s, d_loss: 0.20588808, g_loss: 2.498

Epoch: [ 2/300] [  20/ 115] time: 0.8268s, d_loss: 0.23558933, g_loss: 2.30855274, rnn_loss: 0.03417721
 ** Epoch 2 took 20.184529s
Epoch: [ 2/300] [  21/ 115] time: 0.7542s, d_loss: 0.18976220, g_loss: 2.60201955, rnn_loss: 0.07610266
 ** Epoch 2 took 21.155114s
Epoch: [ 2/300] [  22/ 115] time: 0.7410s, d_loss: 0.60373694, g_loss: 1.08416390, rnn_loss: 0.06147984
 ** Epoch 2 took 22.104573s
Epoch: [ 2/300] [  23/ 115] time: 0.7420s, d_loss: 0.39070135, g_loss: 1.36771405, rnn_loss: 0.04952145
 ** Epoch 2 took 23.054068s
Epoch: [ 2/300] [  24/ 115] time: 0.7491s, d_loss: 0.56890339, g_loss: 2.59973288, rnn_loss: 0.09958285
 ** Epoch 2 took 24.014528s
Epoch: [ 2/300] [  25/ 115] time: 0.7680s, d_loss: 0.35052180, g_loss: 2.22805095, rnn_loss: 0.07900521
 ** Epoch 2 took 24.983950s
Epoch: [ 2/300] [  26/ 115] time: 0.7450s, d_loss: 0.49299970, g_loss: 1.33544838, rnn_loss: 0.07381631
 ** Epoch 2 took 25.930420s
Epoch: [ 2/300] [  27/ 115] time: 0.7470s, d_loss: 0.30982071, g_loss: 2.150

...

Epoch: [297/300] [  42/ 115] time: 0.7270s, d_loss: 0.13765840, g_loss: 4.82657099, rnn_loss: 0.00000000
 ** Epoch 297 took 44.213176s
Epoch: [297/300] [  43/ 115] time: 0.7816s, d_loss: 0.08110712, g_loss: 4.49554157, rnn_loss: 0.00000000
 ** Epoch 297 took 45.249080s
Epoch: [297/300] [  44/ 115] time: 0.7040s, d_loss: 0.18151735, g_loss: 3.82183433, rnn_loss: 0.00000000
 ** Epoch 297 took 46.186739s
Epoch: [297/300] [  45/ 115] time: 0.6892s, d_loss: 0.01602194, g_loss: 4.61049509, rnn_loss: 0.00000000
 ** Epoch 297 took 47.172187s
Epoch: [297/300] [  46/ 115] time: 0.8348s, d_loss: 0.36433578, g_loss: 1.51091540, rnn_loss: 0.00000000
 ** Epoch 297 took 48.239385s
Epoch: [297/300] [  47/ 115] time: 0.6921s, d_loss: 0.65050536, g_loss: 6.72120953, rnn_loss: 0.00000000
 ** Epoch 297 took 49.175881s
Epoch: [297/300] [  48/ 115] time: 0.6877s, d_loss: 0.09685223, g_loss: 4.82943535, rnn_loss: 0.00000000
 ** Epoch 297 took 50.151878s
Epoch: [297/300] [  49/ 115] time: 0.7974s, d_loss: 0.0

Epoch: [297/300] [ 103/ 115] time: 0.6994s, d_loss: 0.02750848, g_loss: 3.62283850, rnn_loss: 0.00000000
 ** Epoch 297 took 106.915237s
Epoch: [297/300] [ 104/ 115] time: 0.8399s, d_loss: 0.52269888, g_loss: 6.17785692, rnn_loss: 0.00000000
 ** Epoch 297 took 108.010817s
Epoch: [297/300] [ 105/ 115] time: 0.7965s, d_loss: 0.56624573, g_loss: 6.61066675, rnn_loss: 0.00000000
 ** Epoch 297 took 109.069095s
Epoch: [297/300] [ 106/ 115] time: 0.7421s, d_loss: 0.72700441, g_loss: 2.50470257, rnn_loss: 0.00000000
 ** Epoch 297 took 110.061976s
Epoch: [297/300] [ 107/ 115] time: 0.7120s, d_loss: 0.03993836, g_loss: 2.65425014, rnn_loss: 0.00000000
 ** Epoch 297 took 111.047246s
Epoch: [297/300] [ 108/ 115] time: 0.8360s, d_loss: 0.03902435, g_loss: 3.46056795, rnn_loss: 0.00000000
 ** Epoch 297 took 112.119098s
Epoch: [297/300] [ 109/ 115] time: 0.7433s, d_loss: 0.41413474, g_loss: 6.29648590, rnn_loss: 0.00000000
 ** Epoch 297 took 113.106799s
Epoch: [297/300] [ 110/ 115] time: 0.6829s, d_lo

Epoch: [298/300] [  49/ 115] time: 0.8475s, d_loss: 0.39729887, g_loss: 2.43191481, rnn_loss: 0.00000000
 ** Epoch 298 took 51.388251s
Epoch: [298/300] [  50/ 115] time: 0.7354s, d_loss: 0.20291060, g_loss: 2.93251848, rnn_loss: 0.00000000
 ** Epoch 298 took 52.360075s
Epoch: [298/300] [  51/ 115] time: 0.7321s, d_loss: 0.12931171, g_loss: 3.35958433, rnn_loss: 0.00000000
 ** Epoch 298 took 53.369865s
Epoch: [298/300] [  52/ 115] time: 0.8764s, d_loss: 0.04268564, g_loss: 4.04412508, rnn_loss: 0.00000000
 ** Epoch 298 took 54.460703s
Epoch: [298/300] [  53/ 115] time: 0.8160s, d_loss: 0.08022592, g_loss: 3.73862934, rnn_loss: 0.00000000
 ** Epoch 298 took 55.471162s
Epoch: [298/300] [  54/ 115] time: 0.6712s, d_loss: 0.03326029, g_loss: 4.45483875, rnn_loss: 0.00000000
 ** Epoch 298 took 56.332889s
Epoch: [298/300] [  55/ 115] time: 0.6672s, d_loss: 0.13160747, g_loss: 3.38971710, rnn_loss: 0.00000000
 ** Epoch 298 took 57.268356s
Epoch: [298/300] [  56/ 115] time: 0.8807s, d_loss: 0.0

Epoch: [298/300] [ 110/ 115] time: 0.8262s, d_loss: 0.23523311, g_loss: 3.07225585, rnn_loss: 0.00000000
 ** Epoch 298 took 113.424519s
Epoch: [298/300] [ 111/ 115] time: 0.6717s, d_loss: 0.07404517, g_loss: 4.28912163, rnn_loss: 0.00000000
 ** Epoch 298 took 114.309208s
Epoch: [298/300] [ 112/ 115] time: 0.6626s, d_loss: 0.01749447, g_loss: 5.07176065, rnn_loss: 0.00000000
 ** Epoch 298 took 115.251217s
Epoch: [298/300] [ 113/ 115] time: 0.8128s, d_loss: 0.11590631, g_loss: 3.46108627, rnn_loss: 0.00000000
 ** Epoch 298 took 116.286472s
Epoch: [298/300] [ 114/ 115] time: 0.7849s, d_loss: 0.13333330, g_loss: 4.10281849, rnn_loss: 0.00000000
 ** Epoch 298 took 117.294751s
Epoch: [299/300] [   0/ 115] time: 0.6951s, d_loss: 0.19785997, g_loss: 3.47660327, rnn_loss: 0.00000000
 ** Epoch 299 took 0.695112s
Epoch: [299/300] [   1/ 115] time: 0.8278s, d_loss: 0.11018251, g_loss: 3.66307783, rnn_loss: 0.00000000
 ** Epoch 299 took 1.794173s
Epoch: [299/300] [   2/ 115] time: 0.8298s, d_loss: 

Epoch: [299/300] [  56/ 115] time: 0.7391s, d_loss: 0.04584290, g_loss: 6.00278044, rnn_loss: 0.00000000
 ** Epoch 299 took 52.129169s
Epoch: [299/300] [  57/ 115] time: 0.6592s, d_loss: 0.11329307, g_loss: 3.82531309, rnn_loss: 0.00000000
 ** Epoch 299 took 52.981855s
Epoch: [299/300] [  58/ 115] time: 0.6573s, d_loss: 0.17325899, g_loss: 3.86100435, rnn_loss: 0.00000000
 ** Epoch 299 took 53.837620s
Epoch: [299/300] [  59/ 115] time: 0.6602s, d_loss: 0.02134831, g_loss: 4.94036007, rnn_loss: 0.00000000
 ** Epoch 299 took 54.691286s
Epoch: [299/300] [  60/ 115] time: 0.7186s, d_loss: 0.36202902, g_loss: 3.24960423, rnn_loss: 0.00000000
 ** Epoch 299 took 55.631046s
Epoch: [299/300] [  61/ 115] time: 0.7627s, d_loss: 0.10747200, g_loss: 2.66933298, rnn_loss: 0.00000000
 ** Epoch 299 took 56.698913s
Epoch: [299/300] [  62/ 115] time: 0.6922s, d_loss: 0.07000461, g_loss: 3.54135847, rnn_loss: 0.00000000
 ** Epoch 299 took 57.646381s
Epoch: [299/300] [  63/ 115] time: 0.7460s, d_loss: 0.1

In [49]:
    captions = train_captions
    caption = []
    for i in range(len(captions)):
        caption.append(captions[i])
    caption = np.asarray(caption)
    #index = data['ID'].values
    #index = np.asarray(index)

    t_real_caption = tf.placeholder(dtype=tf.int64, shape=[batch_size, None], name='real_caption_input')
    t_z = tf.placeholder(tf.float32, [batch_size, z_dim], name='z_noise')

    net_g = Generator(t_z, rnn_encoder(t_real_caption, is_training=False, reuse=True).outputs,
                    is_training=False, reuse=True)

    sess = tf.Session(config=tf.ConfigProto(allow_soft_placement=True))
    init = tf.global_variables_initializer()
    sess.run(init)

    ckpt = tf.train.get_checkpoint_state(checkpoint_dir)
    if ckpt and ckpt.model_checkpoint_path:
        loader = tf.train.Saver(var_list=tf.global_variables())
        load_step = int(os.path.basename(ckpt.model_checkpoint_path).split('-')[1])
        load(loader, sess, ckpt.model_checkpoint_path)
    else:
        print('no checkpoints find.')

    n_caption_test = len(caption)
    n_batch_epoch = int(n_caption_test / batch_size) + 1

    ## repeat
    caption = np.tile(caption, (2, 1))
    #index = np.tile(index, 2)

    #assert index[0] == index[n_caption_test]

    for i in range(n_batch_epoch):
        test_cap = caption[i*batch_size: (i+1)*batch_size]

        z = np.random.normal(loc=0.0, scale=1.0, size=(batch_size, z_dim)).astype(np.float32)
        gen = sess.run(net_g.outputs, feed_dict={t_real_caption: test_cap, t_z: z})
        for j in range(batch_size):
            save_images(np.expand_dims(gen[j], axis=0), [1, 1],r"C:\Users\Stuti pandey\Documents\inference\inference_{:04d}.png".format(i*batch_size + j))

INFO:tensorflow:Restoring parameters from ./checkpoint\model.ckpt-290
Restored model parameters from ./checkpoint\model.ckpt-290
